In [188]:
#rain precipitation from TRMM/GPM has been normalized into HDF5 by IMERG
#example
#wget https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/10/21/imerg/3B-HHR.MS.MRG.3IMERG.20121021-S170000-E172959.1020.V06B.HDF5
#

from ipynb.fs.full.utils import *
from glob import glob
import os
import requests
from urllib.parse import urlparse
from bs4 import BeautifulSoup
import re
import csv


diameter = 5



In [189]:
def parse_html(html_file):
    '''
    parse html to get file list
    '''       
    with open(html_file, 'r') as input:
        soup = BeautifulSoup(input, "html.parser").find_all(lambda t: t.name == "a" and t.text.startswith('3B'))
        filelist = []
        for it in soup:
            filelist.append(it["href"])
        return filelist
    

def download_filelist(folder, url):
    print ('downloading to ', folder)
    
    username = 'xiaogang.liu1@gmail.com'
    password = 'xiaogang.liu1@gmail.com'

    filename = folder + 'index.html'
    
    r = requests.get(url, auth = (username, password))

    if r.status_code == 200:
        print ('writing to', filename)
        with open(filename, 'wb') as out:
            for bits in r.iter_content():
                out.write(bits)
                
        file_list = parse_html(filename)
        
        return file_list
        
def download_file(folder, url, filename):
     
    username = 'xiaogang.liu1@gmail.com'
    password = 'xiaogang.liu1@gmail.com'
    
    print ('downloading file ', url + filename)
    
    r = requests.get(url + filename, auth = (username, password))
    if r.status_code == 200:
        print ('writing to', folder + filename)
        with open(folder + filename, 'wb') as out:
            for bits in r.iter_content():
                out.write(bits)
    else:
        print ('download error ', r.status_code)
    
     
def generate_imerg_url(datestr):
    '''
    compose url using date  'YYYYMMDD'
    '''
    print 
    url = 'https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/' + datestr[0:4] + '/' + datestr[4:6] + '/' + datestr[6:8] + '/imerg/'
    
    print (url)
    return url

    
def get_target_file(filelist, timestr):
    '''
    return file that matches timestamp
    '''
    key = 'S' + timestr
    print (key)
    for it in filelist:
        if key in it:
            return it
    return None

    
def download_imerg(folder):
    json_profile = folder + '/profile.json'
    json_file = open(json_profile)
    d = json.load(json_file)
        
    for it in d['path']:
        print(it)
        
        url = generate_imerg_url(str(it['date']))
        
        filelist = download_filelist(folder, url)
        
        if filelist is None:
            continue
        
        filename = get_target_file(filelist, str(it['time']))  # without path
        if filename is None:
            continue
        
        download_file(folder, url, filename)
        
        #this is the downloaded file
        full_path_filename = folder + filename
        post_processing(it, folder, full_path_filename, it['lg'], it['lt'])

def post_processing(param, folder, full_path_filename, lonstr, latstr): # lon and lat should be read from the path name or given externally
    '''
        1) pick the data only in bounding  box
        2) output to CSV with date_time
        3) remove the downloaded hdf5 files
    '''    
    lon = 0
    lat = 0
    sign = -1.0 if 'W' in lonstr else 1.0
    lon = sign * float(lonstr[:-1])
    sign = -1.0 if 'S' in latstr else 1.0
    lat = sign * float(latstr[:-1])
            
    x = int((lon-longitude[0])*10)
    y = int((lat-latitude[0])*10)
    
    hdf_array = h5py.File(full_path_filename, 'r')
    data = hdf_array['Grid']['precipitationCal'][:, x-5:x+5, y-5:y+5] # 10 by 10, one square degree (#1)

    datestr = str(param['date'])
    timestr = str(param['time'])
    final = np.array([data])

    pathname = folder + 'imerg_precipitation_' + datestr + '_' + timestr + '.npy'
    np.save(pathname, final) # write np array to .npy file with pre-existing file name + datestr + timestr (#2)

    os.remove(full_path_filename) # remove previous .HDF5 file (#3)
  

In [ ]:
#getDayPosition('/home/fun/data/AL182012/profile.json')

hurricanes_folders = glob("/home/fun/data/*/", recursive = True)

for it in hurricanes_folders:
    download_imerg(it)



{'date': 20040803, 'time': '1200', 'category': 'TD', 'lt': '12.9N', 'lg': '53.6W', 'maxwind': '25', 'maxpres': '1010', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/03/imerg/
downloading to  /home/fun/data/AL022004/
writing to /home/fun/data/AL022004/index.html
S1200
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/03/imerg/3B-HHR.MS.MRG.3IMERG.20040803-S120000-E122959.0720.V06B.HDF5
writing to /home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040803-S120000-E122959.0720.V06B.HDF5
{'date': 20040803, 'time': '1800', 'category': 'TD', 'lt': '13.2N', 'lg': '55.4W', 'maxwind': '25', 'maxpres': '1010', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0'

{'date': 20040806, 'time': '0600', 'category': 'WV', 'lt': '17.1N', 'lg': '74.6W', 'maxwind': '25', 'maxpres': '1011', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/06/imerg/
downloading to  /home/fun/data/AL022004/
writing to /home/fun/data/AL022004/index.html
S0600
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/06/imerg/3B-HHR.MS.MRG.3IMERG.20040806-S060000-E062959.0360.V06B.HDF5
writing to /home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040806-S060000-E062959.0360.V06B.HDF5
{'date': 20040806, 'time': '1200', 'category': 'WV', 'lt': '17.2N', 'lg': '76.2W', 'maxwind': '25', 'maxpres': '1011', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0'

{'date': 20040809, 'time': '0000', 'category': 'TD', 'lt': '21.5N', 'lg': '85.5W', 'maxwind': '25', 'maxpres': '1008', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/09/imerg/
downloading to  /home/fun/data/AL022004/
writing to /home/fun/data/AL022004/index.html
S0000
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/09/imerg/3B-HHR.MS.MRG.3IMERG.20040809-S000000-E002959.0000.V06B.HDF5
writing to /home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040809-S000000-E002959.0000.V06B.HDF5
{'date': 20040809, 'time': '0600', 'category': 'TD', 'lt': '22.0N', 'lg': '86.6W', 'maxwind': '30', 'maxpres': '1008', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0'

{'date': 20040811, 'time': '1800', 'category': 'TS', 'lt': '26.4N', 'lg': '89.6W', 'maxwind': '55', 'maxpres': '1001', '34ktne': '45', '34ktse': '60', '34ktsw': '60', '34ktnw': '25', '50ktne': '25', '50ktse': '15', '50ktsw': '15', '50ktnw': '15', '64ktne': '15', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/11/imerg/
downloading to  /home/fun/data/AL022004/
writing to /home/fun/data/AL022004/index.html
S1800
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/11/imerg/3B-HHR.MS.MRG.3IMERG.20040811-S180000-E182959.1080.V06B.HDF5
writing to /home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040811-S180000-E182959.1080.V06B.HDF5
{'date': 20040812, 'time': '0000', 'category': 'TS', 'lt': '27.0N', 'lg': '88.8W', 'maxwind': '50', 'maxpres': '1007', '34ktne': '45', '34ktse': '60', '34ktsw': '60', '34ktnw': '25', '50ktne': '25', '50ktse': '15', '50ktsw': '15', '50ktnw': '1

writing to /home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040814-S000000-E002959.0000.V06B.HDF5
{'date': 20040813, 'time': '1200', 'category': 'TD', 'lt': '12.3N', 'lg': '21.8W', 'maxwind': '30', 'maxpres': '1009', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/13/imerg/
downloading to  /home/fun/data/AL042004/
writing to /home/fun/data/AL042004/index.html
S1200
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2004/08/13/imerg/3B-HHR.MS.MRG.3IMERG.20040813-S120000-E122959.0720.V06B.HDF5
writing to /home/fun/data/AL042004/3B-HHR.MS.MRG.3IMERG.20040813-S120000-E122959.0720.V06B.HDF5
{'date': 20040813, 'time': '1800', 'category': 'TD', 'lt': '12.4N', 'lg': '23.0W', 'maxwind': '30', 'maxpres': '1009', '34ktne': '0', '34ktse': '0', '34ktsw

...

writing to /home/fun/data/AL112012/3B-HHR.MS.MRG.3IMERG.20120901-S000000-E002959.0000.V06B.HDF5
{'date': 20120901, 'time': '0600', 'category': 'HU', 'lt': '34.6N', 'lg': '48.9W', 'maxwind': '65', 'maxpres': '990', '34ktne': '60', '34ktse': '50', '34ktsw': '50', '34ktnw': '40', '50ktne': '50', '50ktse': '30', '50ktsw': '30', '50ktnw': '20', '64ktne': '30', '64ktse': '15', '64ktsw': '15', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/01/imerg/
downloading to  /home/fun/data/AL112012/
writing to /home/fun/data/AL112012/index.html
S0600
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/01/imerg/3B-HHR.MS.MRG.3IMERG.20120901-S060000-E062959.0360.V06B.HDF5
writing to /home/fun/data/AL112012/3B-HHR.MS.MRG.3IMERG.20120901-S060000-E062959.0360.V06B.HDF5
{'date': 20120901, 'time': '1200', 'category': 'TS', 'lt': '36.5N', 'lg': '47.3W', 'maxwind': '60', 'maxpres': '992', '34ktne': '70', '34ktse': '6

writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120829-S000000-E002959.0000.V06B.HDF5
{'date': 20120829, 'time': '0600', 'category': 'LO', 'lt': '13.2N', 'lg': '33.7W', 'maxwind': '25', 'maxpres': '1009', '34ktne': '0', '34ktse': '0', '34ktsw': '0', '34ktnw': '0', '50ktne': '0', '50ktse': '0', '50ktsw': '0', '50ktnw': '0', '64ktne': '0', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/08/29/imerg/
downloading to  /home/fun/data/AL122012/
writing to /home/fun/data/AL122012/index.html
S0600
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/08/29/imerg/3B-HHR.MS.MRG.3IMERG.20120829-S060000-E062959.0360.V06B.HDF5
writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120829-S060000-E062959.0360.V06B.HDF5
{'date': 20120829, 'time': '1200', 'category': 'LO', 'lt': '13.3N', 'lg': '35.6W', 'maxwind': '25', 'maxpres': '1009', '34ktne': '0', '34ktse': '0', '34ktsw

writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120831-S180000-E182959.1080.V06B.HDF5
{'date': 20120901, 'time': '0000', 'category': 'TS', 'lt': '17.1N', 'lg': '52.2W', 'maxwind': '60', 'maxpres': '998', '34ktne': '80', '34ktse': '60', '34ktsw': '60', '34ktnw': '40', '50ktne': '70', '50ktse': '30', '50ktsw': '20', '50ktnw': '0', '64ktne': '30', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/01/imerg/
downloading to  /home/fun/data/AL122012/
writing to /home/fun/data/AL122012/index.html
S0000
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/01/imerg/3B-HHR.MS.MRG.3IMERG.20120901-S000000-E002959.0000.V06B.HDF5
writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120901-S000000-E002959.0000.V06B.HDF5
{'date': 20120901, 'time': '0600', 'category': 'TS', 'lt': '17.6N', 'lg': '53.8W', 'maxwind': '60', 'maxpres': '996', '34ktne': '100', '34ktse': '90'

writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120903-S120000-E122959.0720.V06B.HDF5
{'date': 20120903, 'time': '1800', 'category': 'TS', 'lt': '23.8N', 'lg': '62.8W', 'maxwind': '55', 'maxpres': '990', '34ktne': '180', '34ktse': '160', '34ktsw': '160', '34ktnw': '60', '50ktne': '130', '50ktse': '120', '50ktsw': '100', '50ktnw': '0', '64ktne': '0', '64ktse': '0', '64ktsw': '0', '64ktnw': '0', 'maxwindradius': '0'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/03/imerg/
downloading to  /home/fun/data/AL122012/
writing to /home/fun/data/AL122012/index.html
S1800
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/03/imerg/3B-HHR.MS.MRG.3IMERG.20120903-S180000-E182959.1080.V06B.HDF5
writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120903-S180000-E182959.1080.V06B.HDF5
{'date': 20120904, 'time': '0000', 'category': 'TS', 'lt': '24.2N', 'lg': '62.6W', 'maxwind': '60', 'maxpres': '989', '34ktne': '180', '34ktse':

writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120906-S060000-E062959.0360.V06B.HDF5
{'date': 20120906, 'time': '1200', 'category': 'HU', 'lt': '26.3N', 'lg': '62.4W', 'maxwind': '65', 'maxpres': '983', '34ktne': '160', '34ktse': '170', '34ktsw': '170', '34ktnw': '100', '50ktne': '150', '50ktse': '90', '50ktsw': '60', '50ktnw': '40', '64ktne': '70', '64ktse': '20', '64ktsw': '20', '64ktnw': '15', 'maxwindradius': '15'}
https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/06/imerg/
downloading to  /home/fun/data/AL122012/
writing to /home/fun/data/AL122012/index.html
S1200
downloading file  https://arthurhouhttps.pps.eosdis.nasa.gov/gpmallversions/V06/2012/09/06/imerg/3B-HHR.MS.MRG.3IMERG.20120906-S120000-E122959.0720.V06B.HDF5
writing to /home/fun/data/AL122012/3B-HHR.MS.MRG.3IMERG.20120906-S120000-E122959.0720.V06B.HDF5
{'date': 20120906, 'time': '1800', 'category': 'HU', 'lt': '26.4N', 'lg': '62.3W', 'maxwind': '65', 'maxpres': '982', '34ktne': '160', '34k

In [162]:
#test hdf5 imerg

#imerg_df = pd.read_hdf('/home/fun/data/imerg/3B-HHR.MS.MRG.3IMERG.20121021-S023000-E025959.0150.V06B.HDF5')  

import h5py

f = h5py.File('/home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040803-S180000-E182959.1080.V06B.HDF5', 'r')

for key in f.keys():
    print(key) #Names of the root level object names in HDF5 file - can be groups or datasets.
    print(type(f[key])) # get the object type: usually group or dataset
    
#Get the HDF5 group; key needs to be a group name from above
group = f['Grid']

#Checkout what keys are inside that group.
for key in group.keys():
    print(key)
    
longitude = group['lon'][()] # len 3600, x-axis
latitude = group['lat'][()] # len 1800, y-axis
rain = group['precipitationCal'][()] # array of shape (1, 3600, 1800)

lon = -77.4
lat = 14.3

#print(latitude, clos_coords)
i = int((lat-latitude[0])*10)
j = int((lon-longitude[0])*10)
print(latitude[i], longitude[j], i, j)

rain = rain.reshape(3600, 1800)

sliced = rain[j-5:j+5, i-5:i+5]
sliced.shape

Grid
<class 'h5py._hl.group.Group'>
nv
lonv
latv
time
lon
lat
time_bnds
lon_bnds
lat_bnds
precipitationCal
precipitationUncal
randomError
HQprecipitation
HQprecipSource
HQobservationTime
IRprecipitation
IRkalmanFilterWeight
probabilityLiquidPrecipitation
precipitationQualityIndex
14.25 -77.45 1042 1025


(10, 10)

In [169]:
import numpy as np
filename = '/home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20040803-S180000-E182959.1080.V06B.HDF5'

lon = -77.4
lat = 14.3

#print(latitude, clos_coords)
x = int((lon-longitude[0])*10)
y = int((lat-latitude[0])*10)

hdf_array = h5py.File(filename, 'r')
data = hdf_array['Grid']['precipitationCal'][:, x-5:x+5, y-5:y+5]

data

array([[[0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.]]], dtype=float32)

In [85]:
file = '/home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20121021-S000000-E002959.0000.V06B.HDF5'
len(file)

name = file[:len(file)-5]
name

'/home/fun/data/AL022004/3B-HHR.MS.MRG.3IMERG.20121021-S000000-E002959.0000.V06B'

In [179]:
array = np.load('/home/fun/data/AL022004/imerg_precipitation_20040803_1200.npy')
array

array([[[[ 0.06247815,  0.29016453,  1.0588278 ,  2.2504165 ,
           2.343059  ,  2.4157019 , 10.181723  , 12.900776  ,
          26.127796  , 30.346048  ],
         [ 0.37743443,  0.28462726,  0.28016454,  2.1891775 ,
           2.1970284 ,  9.379759  ,  8.414813  , 19.552551  ,
          24.830242  , 23.657272  ],
         [ 0.39421082,  0.9118869 ,  1.2785861 ,  2.6486425 ,
           2.723851  ,  5.715255  , 10.913759  , 25.128246  ,
          24.038334  , 25.0345    ],
         [ 1.0279177 ,  0.93866324,  1.2685862 ,  1.2039589 ,
           2.5193882 ,  4.1288385 ,  5.5526223 ,  6.9541235 ,
          11.752715  , 21.643759  ],
         [ 1.1708999 ,  1.1753626 ,  1.3354396 ,  1.3797377 ,
           1.9213829 ,  4.1697483 ,  5.4864163 ,  7.268257  ,
           9.392678  , 11.334448  ],
         [ 1.6964267 ,  1.4473368 ,  1.3636196 ,  1.3289921 ,
           1.7290797 ,  2.1481695 ,  2.4771826 ,  2.4582572 ,
           2.5453625 ,  6.917589  ],
         [ 3.4169512 ,  2.0160208 